In [219]:
class superelliptic:
    def __init__(self, f, m, p):
        R.<x> = PolynomialRing(GF(p))
        self.polynomial = R(f)
        self.exponent = m
        self.characteristic = p
        
       
    def __repr__(self):
        f = self.polynomial
        m = self.exponent
        p = self.characteristic
        return 'Superelliptic curve with the equation y^' + str(m) + ' = ' + str(f)+' over finite field with ' + str(p) + ' elements.'
    
    def genus(self):
        r = self.polynomial.degree()
        m = self.exponent
        delta = GCD(r, m)
        return 1/2*((r-1)*(m-1) - delta + 1)
    
    def basis_holomorphic_differentials(self, j = 'all'):
        f = self.polynomial
        m = self.exponent
        p = self.characteristic
        r = f.degree()
        delta = GCD(r, m)
        
        basis = {}
        if j == 'all':
            k = 0
            for i in range(1, r):
                for j in range(1, m):
                    if (r*j - m*i >= delta):
                        basis[k] = superelliptic_form(C, x^(i-1)/y^j)
                        k = k+1
            return basis
        else:
            k = 0
            for i in range(1, r):
                if (r*j - m*i >= delta):
                    basis[k] = superelliptic_form(C, x^(i-1)/y^j)
                    k = k+1
            return basis
        
def reduction(C, g):
    p = C.characteristic
    R.<x, y> = PolynomialRing(GF(p), 2)
    RR = FractionField(R)
    f = C.polynomial
    r = f.degree()
    m = C.exponent
    g = RR(g)
    g1 = g.numerator()
    g2 = g.denominator()
    
    R1.<x> = PolynomialRing(GF(p))
    R2 = FractionField(R1)
    R3.<y> = PolynomialRing(R2)    
    (A, B, C) = xgcd(R3(g2), R3(y^m - f))
    g = R3(g1*B/A)
    
    while(g.degree(R(y)) >= m):
        d = g.degree(R(y))
        G = g.coefficient(R(y^d))
        i = floor(d/m)
        g = g - G*y^d + f^i * y^(d%m) *G
    
    return(R3(g))

def reduction_form(C, g):
    p = C.characteristic
    R.<x, y> = PolynomialRing(GF(p), 2)
    RR = FractionField(R)
    f = C.polynomial
    r = f.degree()
    m = C.exponent
    g = reduction(C, g)

    g1 = RR(0)
    R1.<x> = PolynomialRing(GF(p))
    R2 = FractionField(R1)
    R3.<y> = PolynomialRing(R2)
    
    g = R3(g)
    for j in range(0, m):
        G = g.coefficients(sparse = false)[j]
        g1 += RR(y^(j-m)*f*G)
        
    return(g1)
        
class superelliptic_function:
    def __init__(self, C, g):
        R.<x, y> = PolynomialRing(GF(p), 2)
        RR = FractionField(R)
        f = C.polynomial
        r = f.degree()
        m = C.exponent
        
        self.curve = C
        g = reduction(C, g)
        self.function = g
        
    def __repr__(self):
        return str(self.function)
    
    def jth_component(self, j):
        g = self.function
        R.<x, y> = PolynomialRing(GF(p), 2)
        g = R(g)
        return g.coefficient(y^j)
    
    def __add__(self, other):
        C = self.curve
        g1 = self.function
        g2 = other.function
        g = reduction(C, g1 + g2)
        return superelliptic_function(C, g)
    
    def __sub__(self, other):
        C = self.curve
        g1 = self.function
        g2 = other.function
        g = reduction(C, g1 - g2)
        return superelliptic_function(C, g)
    
    def __mul__(self, other):
        C = self.curve
        g1 = self.function
        g2 = other.function
        g = reduction(C, g1 * g2)
        return superelliptic_function(C, g)
    
    def __truediv__(self, other):
        C = self.curve
        g1 = self.function
        g2 = other.function
        g = reduction(C, g1 / g2)
        return superelliptic_function(C, g)
    
def diffn(self):
    C = self.curve
    f = C.polynomial
    m = C.exponent
    g = self.function
    A = g.derivative(x)
    B = g.derivative(y)*f.derivative(x)/(m*y^(m-1))
    return superelliptic_form(C, A+B)
        
class superelliptic_form:
    def __init__(self, C, g):
        R.<x, y> = PolynomialRing(GF(p), 2)
        RR = FractionField(R)
        g = RR(reduction_form(C, g))
        self.form = g
        self.curve = C      
        
    def __add__(self, other):
        C = self.curve
        g1 = self.form
        g2 = other.form
        g = reduction(C, g1 + g2)
        return superelliptic_form(C, g)
    
    def __sub__(self, other):
        C = self.curve
        g1 = self.form
        g2 = other.form
        g = reduction(C, g1 - g2)
        return superelliptic_form(C, g)
    
    def __repr__(self):
        g = self.form
        if len(str(g)) == 1:
            return str(g) + ' dx'
        return '('+str(g) + ') dx'
    
    def jth_component(self, j):
        g = self.form
        R.<x, y> = PolynomialRing(GF(p), 2)
        g = R(g)
        return g.coefficient(y^j)

In [220]:
C = superelliptic(x^3 + x + 2, 2, 5)
C.basis_holomorphic_differentials()

{0: (1/y) dx}

In [179]:
A.degree(y)

0

In [180]:
p = 5
R.<x, y> = PolynomialRing(GF(p), 2)
g = x^6*y^2 + y^2

In [181]:
omega = diffn(superelliptic_function(C, y^2))

In [183]:
omega.jth_component(0)

-2*x^2 + 1

In [33]:
R.<x, y> = PolynomialRing(GF(p), 2)
g1 = x^3*y^7 + x^2*y^9
g2 = x^2*y + y^6
R1.<x> = PolynomialRing(GF(p))
R2 = FractionField(R1)
R3.<y> = PolynomialRing(R2)

xgcd(R3(g1), R3(g2))[1]*R3(g1) + xgcd(R3(g1), R3(g2))[2]*R3(g2)

y

In [39]:
H = HyperellipticCurve(x^5 - x + 1)

In [40]:
H

Hyperelliptic Curve over Finite Field of size 5 defined by y^2 = x^5 + 4*x + 1

In [84]:
f = x^3 + x + 2

In [86]:
f.derivative(x)

-2*x^2 + 1

In [213]:
R1.<x> = PolynomialRing(GF(p))
R2 = FractionField(R1)
R3.<y> = PolynomialRing(R2)
g = y^2/x + y/(x+1)    

In [218]:
g.coefficients(sparse = false)

[0, 1/(x + 1), 1/x]